### Library import

In [6]:
import os 
import json 
import pandas as pd 
import sys

### Path section

In [1]:
# PATH
PATH_input = r"C:\Users\mchahdil\Desktop\compare_study\\input_files"
PATH_output = r"C:\Users\mchahdil\Desktop\compare_study\\output_files"

PATH_patient_folder = r"C:\Users\mchahdil\Desktop\data_patient\json_raw\\"

PATH_patient_sim = r"C:\Users\mchahdil\Desktop\compare_study\\output_files\phenopacket\\"


orpha_pd = PATH_input + "/orphanet_files/en_product4.xml"


# Get  case 

In [78]:
#pd_phenopacket = pd.read_excel(str(PATH_output)+"/df_hpo_solved_confirmed.xlsx",engine='openpyxl',index_col=0 )
pd_phenopacket = pd.read_excel(str(PATH_output)+"/df_hpo_simulated.xlsx",engine='openpyxl',index_col=0 )

pd_phenopacket


phenopacket         hpo  nb_hpo
0       Pf001003  HP:0003198      12
1       Pf001003  HP:0002186      12
2       Pf001003  HP:0011448      12
3       Pf001003  HP:0001290      12
4       Pf001003  HP:0002459      12
...          ...         ...     ...
4219    Po008924  HP:0003323      11
4220    Po008924  HP:0008997      11
4221    Po008924  HP:0000467      11
4222    Po008924  HP:0001371      11
4223    Po008924  HP:0002751      11

[4224 rows x 3 columns]

# Hpo3 


### import hpo library

In [79]:
from pyhpo import stats, Ontology, HPOSet
# initilize the Ontology
Ontology()

### Get hpo form Orpha  


In [80]:
import xmltodict

orphacode_info=dict()

with open(orpha_pd) as pd_xml:
    root = xmltodict.parse(pd_xml.read())
xml_dict = root['JDBOR']['HPODisorderSetStatusList']['HPODisorderSetStatus']
for one_dict in xml_dict:
    hpo_list = []
    section_disorder = one_dict['Disorder']
    #print(section_disorder['OrphaCode'])
    section_hpo = section_disorder['HPODisorderAssociationList']
    #print(section_hpo.keys())
    # because sometime HPODisorderAssociation dict don't exist 
    if "HPODisorderAssociation" in section_hpo.keys():    
        for one_hpodict in section_hpo['HPODisorderAssociation']:
            hpo_id = one_hpodict['HPO']['HPOId']
            hpo_list.append(hpo_id)
    orphacode_info[section_disorder['OrphaCode']] = hpo_list


get df hpo

### Select for each phenopackets all orphacodes from hpo3 and build a list of dict for each phenopackets

In [83]:
# list of phenoapcket
patients = pd_phenopacket["phenopacket"].drop_duplicates().tolist()
print('Nb of patients : {}'.format(len(patients)))

Nb of patients : 358


In [84]:
type_score = "resnik"

In [85]:
hpo3_case_ORPHA = []
dict_hpo3_case_ORPHA = {}
p = 0
o = 0

for onep in patients:
    try: 
        minidf = pd_phenopacket[pd_phenopacket["phenopacket"] == onep]
        list_hpo =minidf["hpo"].drop_duplicates().tolist()
        one_pheno_HPOSet = HPOSet.from_queries(list_hpo)

        for key in orphacode_info.keys():
            try:
                one_orpha_HPOSet = HPOSet.from_queries(orphacode_info[key])


                #the_score = one_pheno_HPOSet.similarity(one_orpha_HPOSet,method='resnik')
                the_score = one_pheno_HPOSet.similarity(one_orpha_HPOSet,method=type_score)

                #print("{} - {} :  {} ".format(str("ORPHA:")+key,onep,the_score))
                hpo3_case_ORPHA.append((onep,str("ORPHA:")+key,the_score))
            except RuntimeError:
                #print("{} - {} the orphacode have unknow HPO term for hpo3, no resnik sim".format(onep,str("ORPHA:")+key))
                o=o+1
        dict_hpo3_case_ORPHA[onep] = hpo3_case_ORPHA
        hpo3_case_ORPHA = []

    except RuntimeError:
        #print("{} have unknow HPO term for hpo3".format(onep))
        p=p+1
    
                        
#df_hpo3_case_ORPHA = pd.DataFrame(hpo3_case_ORPHA, columns=["phenopacket",'ORPHAcode','score'])
print("{} phenopackets have unknow hpo and {} orphacodes have unknow hpo".format(p,o))
#dict_hpo3_case_ORPHA

In [68]:
dict_hpo3_case_ORPHA

{'P0001068': [('P0001068', 'ORPHA:58', 1.2410002776099656),
  ('P0001068', 'ORPHA:61', 1.0420779180391417),
  ('P0001068', 'ORPHA:93', 0.9986960143506498),
  ('P0001068', 'ORPHA:585', 0.778973162211137),
  ('P0001068', 'ORPHA:118', 0.8940933655501513),
  ('P0001068', 'ORPHA:141', 0.9276566332194761),
  ('P0001068', 'ORPHA:213', 1.1471805745671837),
  ('P0001068', 'ORPHA:349', 0.8582948367699066),
  ('P0001068', 'ORPHA:366', 0.8094539732564698),
  ('P0001068', 'ORPHA:371', 1.8527647204450117),
  ('P0001068', 'ORPHA:583', 1.0137733688055912),
  ('P0001068', 'ORPHA:812', 1.4306953115255938),
  ('P0001068', 'ORPHA:578', 0.9418001792672998),
  ('P0001068', 'ORPHA:577', 0.4050906520086145),
  ('P0001068', 'ORPHA:796', 1.096714285159736),
  ('P0001068', 'ORPHA:584', 0.7636974440524622),
  ('P0001068', 'ORPHA:461', 0.14064258879611438),
  ('P0001068', 'ORPHA:881', 0.5578547689209251),
  ('P0001068', 'ORPHA:848', 1.0131432675512437),
  ('P0001068', 'ORPHA:586', 0.3175509830604184),
  ('P0001068

### Build a dict of df 
for each patient solved confirmed build a df filter the df 


In [69]:
# pour contrer le probleme faire un dict de list réaliser precedement et ICI faire un df a chaque fois et filtrer 
# puis add dans un new autre dict
dict_of_hpo3_df = {}

for key,listvalue in dict_hpo3_case_ORPHA.items():
    #print(key)
    # build the df 
    df_values = pd.DataFrame(listvalue, columns=["phenopacket",'ORPHAcode',type_score])
    # select subset of df 
    df_op = df_values[df_values['phenopacket'] == key]
    # sort by score
    df_op = df_op.sort_values(type_score,ascending=False)
    # keep the top 50
    df_op = df_op.head(50)
    df_op.reset_index(drop=True)
    dict_of_hpo3_df[key] = df_op
    df_op= pd.DataFrame([], columns=["phenopacket",'ORPHAcode',type_score])

dict_of_hpo3_df

{'P0001068':      phenopacket     ORPHAcode    resnik
 2900    P0001068  ORPHA:178400  3.746146
 3182    P0001068  ORPHA:482601  3.606251
 2884    P0001068  ORPHA:399096  3.551814
 3184    P0001068   ORPHA:45448  3.467137
 2898    P0001068  ORPHA:399086  3.320901
 3186    P0001068   ORPHA:63273  3.287160
 4102    P0001068   ORPHA:98856  3.273925
 3187    P0001068   ORPHA:98897  3.212189
 3543    P0001068  ORPHA:435387  3.187800
 4146    P0001068  ORPHA:101097  3.180463
 3519    P0001068   ORPHA:99950  3.172447
 3240    P0001068   ORPHA:99953  3.166494
 2804    P0001068  ORPHA:139536  3.084351
 1880    P0001068     ORPHA:602  3.051287
 3522    P0001068  ORPHA:101085  3.042573
 3188    P0001068   ORPHA:98912  3.038341
 3361    P0001068  ORPHA:466768  3.031939
 2823    P0001068  ORPHA:488333  3.024581
 2894    P0001068  ORPHA:399103  3.020800
 3548    P0001068  ORPHA:101077  3.003282
 2768    P0001068   ORPHA:90103  2.995383
 2590    P0001068  ORPHA:206549  2.962150
 1200    P0001068     

### Build THE final df

In [70]:

all_interractions=[]


for key,dfval in dict_of_hpo3_df.items():
    #print("set the df for the patient {}".format(key))
    dict_df_one_P_hpo3 = dfval.to_dict('index')

    i = 0 # for the rank
    for value in dict_df_one_P_hpo3.values():
        hpo3_onepheno = value['phenopacket']
        hpo3_oneorpha= value['ORPHAcode']
        hpo3_onescore= value[type_score]

        i = i + 1
        
        all_interractions.append((hpo3_onepheno,hpo3_oneorpha,hpo3_onescore,i))



df_hpo3_solvedCO = pd.DataFrame(all_interractions, columns=["phenopacket",'ORPHAcode',type_score,'rank_hpo3'])

In [72]:

# df_hpo3_solvedCO.to_excel(PATH_output+"/df_hpo3_lin.xlsx")
df_hpo3_solvedCO.to_excel(PATH_output+"/df_hpo3_"+str(type_score)+".xlsx")

### Normalize the score col resnik only 

get the parameter needs for the score normalization

In [21]:
score_min_tot = df_hpo3_solvedCO[type_score].min()
score_max_tot = df_hpo3_solvedCO[type_score].max()
score_mean_tot = df_hpo3_solvedCO[type_score].mean()
score_std_tot = df_hpo3_solvedCO[type_score].std()

### change the initale df to add the col score normalised which is calculated in the loop

In [22]:
dict_df_hpo3_solvedCO = df_hpo3_solvedCO.to_dict('index')
all_interractions = []

for value in dict_df_hpo3_solvedCO.values():
    hpo3_onepheno = value['phenopacket']
    hpo3_oneorpha= value['ORPHAcode']
    hpo3_onescore= value[type_score]
    hpo3_onerank= value['rank_hpo3']
    hpo3_onescore_norm = ((hpo3_onescore - score_min_tot)/ (score_max_tot - score_min_tot))

    all_interractions.append((hpo3_onepheno,hpo3_oneorpha,hpo3_onescore,hpo3_onescore_norm,hpo3_onerank))

df_hpo3= pd.DataFrame(all_interractions, columns=["phenopacket",'ORPHAcode_hpo3',type_score,'score_norm_hpo3','rank_hpo3'])

df_hpo3

phenopacket ORPHAcode_hpo3    resnik  score_norm_hpo3  rank_hpo3
0       P0001068   ORPHA:178400  3.746146         0.892018          1
1       P0001068   ORPHA:482601  3.606251         0.837982          2
2       P0001068   ORPHA:399096  3.551814         0.816956          3
3       P0001068    ORPHA:45448  3.467137         0.784249          4
4       P0001068   ORPHA:399086  3.320901         0.727764          5
...          ...            ...       ...              ...        ...
6995    P0022261    ORPHA:98905  2.172371         0.284136         46
6996    P0022261   ORPHA:100984  2.165407         0.281446         47
6997    P0022261    ORPHA:59135  2.157850         0.278527         48
6998    P0022261    ORPHA:99939  2.156802         0.278122         49
6999    P0022261   ORPHA:324442  2.149357         0.275247         50

[7000 rows x 5 columns]

In [23]:
df_hpo3.to_excel("df_hpo3_resnik.xlsx")